In [1]:
# coding=utf-8
"""
This module contains the tests for the exchanges classes
"""
from fastlane_bot import Bot, Config
from fastlane_bot.bot import CarbonBot
from fastlane_bot.tools.cpc import ConstantProductCurve as CPC
from fastlane_bot.events.exchanges import UniswapV2, UniswapV3, SushiswapV2, CarbonV1, BancorV3
from fastlane_bot.events.interface import QueryInterface
from fastlane_bot.helpers.poolandtokens import PoolAndTokens
from fastlane_bot.helpers import TradeInstruction, TxReceiptHandler, TxRouteHandler, TxSubmitHandler, TxHelpers, TxHelper
from fastlane_bot.events.manager import Manager
from fastlane_bot.events.interface import QueryInterface
import pytest
import math
print("{0.__name__} v{0.__VERSION__} ({0.__DATE__})".format(CPC))
print("{0.__name__} v{0.__VERSION__} ({0.__DATE__})".format(Bot))
print("{0.__name__} v{0.__VERSION__} ({0.__DATE__})".format(UniswapV2))
print("{0.__name__} v{0.__VERSION__} ({0.__DATE__})".format(UniswapV3))
print("{0.__name__} v{0.__VERSION__} ({0.__DATE__})".format(SushiswapV2))
print("{0.__name__} v{0.__VERSION__} ({0.__DATE__})".format(CarbonV1))
print("{0.__name__} v{0.__VERSION__} ({0.__DATE__})".format(BancorV3))
from fastlane_bot.testing import *

plt.style.use('seaborn-dark')
plt.rcParams['figure.figsize'] = [12,6]
from fastlane_bot import __VERSION__
require("3.0", __VERSION__)

ConstantProductCurve v2.10.1 (07/May/2023)
CarbonBot v3-b2.2 (20/June/2023)
UniswapV2 v0.0.1 (2023-07-03)
UniswapV3 v0.0.1 (2023-07-03)
SushiswapV2 v0.0.1 (2023-07-03)
CarbonV1 v0.0.1 (2023-07-03)
BancorV3 v0.0.1 (2023-07-03)
imported m, np, pd, plt, os, sys, decimal; defined iseq, raises, require


C:\Users\Kveen\AppData\Local\Temp\ipykernel_33400\4135921317.py:25: MatplotlibDeprecationWarning: The seaborn styles shipped by Matplotlib are deprecated since 3.6, as they no longer correspond to the styles shipped by seaborn. However, they will remain available as 'seaborn-v0_8-<style>'. Alternatively, directly use the seaborn API instead.
  plt.style.use('seaborn-dark')


Version = 3-b2.2 [requirements >= 3.0 is met]


In [2]:
C = cfg = Config.new(config=Config.CONFIG_MAINNET)
assert (C.NETWORK == C.NETWORK_MAINNET)
assert (C.PROVIDER == C.PROVIDER_ALCHEMY)
setup_bot = CarbonBot(ConfigObj=C)

In [3]:
import json

pools = None
with open('latest_pool_data.json') as f:
    pools = json.load(f)
pools = [pool for pool in pools]

In [4]:
pools[0]
static_pools = pools

In [5]:
print(pools[0])
print(static_pools[0])

{'cid': '0xddf6fc281404ba860af9a19ffeff6f69395378d793f873065cf19f19fa9b1c65', 'last_updated': nan, 'last_updated_block': 17656207, 'descr': 'uniswap_v2 BOBO-5295/WETH-6Cc2 0.003', 'pair_name': 'BOBO-5295/WETH-6Cc2', 'exchange_name': 'uniswap_v2', 'fee': 3000, 'fee_float': 0.003, 'address': '0xe945683B3462D2603a18BDfBB19261C6a4f03aD1', 'anchor': nan, 'tkn0_address': '0xB90B2A35C65dBC466b04240097Ca756ad2005295', 'tkn1_address': '0xC02aaA39b223FE8D0A0e5C4F27eAD9083C756Cc2', 'tkn0_key': 'BOBO-5295', 'tkn1_key': 'WETH-6Cc2', 'tkn0_decimals': 18.0, 'tkn1_decimals': 18.0, 'exchange_id': nan, 'tkn0_symbol': 'BOBO', 'tkn1_symbol': 'WETH', 'timestamp': '15:40:32', 'tkn0_balance': 1434030247235265560210480530773, 'tkn1_balance': 148902824268025040023, 'liquidity': nan, 'sqrt_price_q96': nan, 'tick': nan, 'tick_spacing': 60, 'exchange': 'uniswap_v2'}
{'cid': '0xddf6fc281404ba860af9a19ffeff6f69395378d793f873065cf19f19fa9b1c65', 'last_updated': nan, 'last_updated_block': 17656207, 'descr': 'uniswap_

In [6]:
state = pools
exchanges = list({ex['exchange_name'] for ex in state})
db = QueryInterface(state=state, ConfigObj=C, exchanges=exchanges)
setup_bot.db = db

In [7]:
print(state[0])

{'cid': '0xddf6fc281404ba860af9a19ffeff6f69395378d793f873065cf19f19fa9b1c65', 'last_updated': nan, 'last_updated_block': 17656207, 'descr': 'uniswap_v2 BOBO-5295/WETH-6Cc2 0.003', 'pair_name': 'BOBO-5295/WETH-6Cc2', 'exchange_name': 'uniswap_v2', 'fee': 3000, 'fee_float': 0.003, 'address': '0xe945683B3462D2603a18BDfBB19261C6a4f03aD1', 'anchor': nan, 'tkn0_address': '0xB90B2A35C65dBC466b04240097Ca756ad2005295', 'tkn1_address': '0xC02aaA39b223FE8D0A0e5C4F27eAD9083C756Cc2', 'tkn0_key': 'BOBO-5295', 'tkn1_key': 'WETH-6Cc2', 'tkn0_decimals': 18.0, 'tkn1_decimals': 18.0, 'exchange_id': nan, 'tkn0_symbol': 'BOBO', 'tkn1_symbol': 'WETH', 'timestamp': '15:40:32', 'tkn0_balance': 1434030247235265560210480530773, 'tkn1_balance': 148902824268025040023, 'liquidity': nan, 'sqrt_price_q96': nan, 'tick': nan, 'tick_spacing': 60, 'exchange': 'uniswap_v2'}


In [8]:
print(pools[0])

{'cid': '0xddf6fc281404ba860af9a19ffeff6f69395378d793f873065cf19f19fa9b1c65', 'last_updated': nan, 'last_updated_block': 17656207, 'descr': 'uniswap_v2 BOBO-5295/WETH-6Cc2 0.003', 'pair_name': 'BOBO-5295/WETH-6Cc2', 'exchange_name': 'uniswap_v2', 'fee': 3000, 'fee_float': 0.003, 'address': '0xe945683B3462D2603a18BDfBB19261C6a4f03aD1', 'anchor': nan, 'tkn0_address': '0xB90B2A35C65dBC466b04240097Ca756ad2005295', 'tkn1_address': '0xC02aaA39b223FE8D0A0e5C4F27eAD9083C756Cc2', 'tkn0_key': 'BOBO-5295', 'tkn1_key': 'WETH-6Cc2', 'tkn0_decimals': 18.0, 'tkn1_decimals': 18.0, 'exchange_id': nan, 'tkn0_symbol': 'BOBO', 'tkn1_symbol': 'WETH', 'timestamp': '15:40:32', 'tkn0_balance': 1434030247235265560210480530773, 'tkn1_balance': 148902824268025040023, 'liquidity': nan, 'sqrt_price_q96': nan, 'tick': nan, 'tick_spacing': 60, 'exchange': 'uniswap_v2'}


In [9]:
static_pool_data_filename = "static_pool_data"

static_pool_data = pd.read_csv(f"fastlane_bot/data/{static_pool_data_filename}.csv", low_memory=False)
    
uniswap_v2_event_mappings = pd.read_csv("fastlane_bot/data/uniswap_v2_event_mappings.csv", low_memory=False)
        
tokens = pd.read_csv("fastlane_bot/data/tokens.csv", low_memory=False)
        
exchanges = "carbon_v1,bancor_v3,uniswap_v3,uniswap_v2,sushiswap_v2"

exchanges = exchanges.split(",")
arb_mode = "bancor_v3"

alchemy_max_block_fetch = 20

In [10]:
static_pool_data["cid"] = [
        cfg.w3.keccak(text=f"{row['descr']}").hex()
        for index, row in static_pool_data.iterrows()
    ]


In [11]:
# Filter out pools that are not in the supported exchanges
static_pool_data = [
    row for index, row in static_pool_data.iterrows()
    if row["exchange_name"] in exchanges
]

static_pool_data = pd.DataFrame(static_pool_data)

In [12]:
static_pool_data['exchange_name'].unique()

array(['uniswap_v3', 'bancor_v3', 'uniswap_v2', 'sushiswap_v2'],
      dtype=object)

In [13]:
from joblib import Parallel, delayed

# Initialize data fetch manager
mgr = Manager(
    web3=cfg.w3,
    cfg=cfg,
    pool_data=static_pool_data.to_dict(orient="records"),
    SUPPORTED_EXCHANGES=exchanges,
    alchemy_max_block_fetch=alchemy_max_block_fetch,
    uniswap_v2_event_mappings=uniswap_v2_event_mappings,
    tokens=tokens.to_dict(orient="records"),
)

# Add initial pools for each row in the static_pool_data
start_time = time.time()
Parallel(n_jobs=-1, backend="threading")(
    delayed(mgr.add_pool_to_exchange)(row) for row in mgr.pool_data
)
cfg.logger.info(f"Time taken to add initial pools: {time.time() - start_time}")

# check if any duplicate cid's exist in the pool data
mgr.deduplicate_pool_data()
cids = [pool["cid"] for pool in mgr.pool_data]
assert len(cids) == len(set(cids)), "duplicate cid's exist in the pool data"

2023-07-09 17:21:48,346 [fastlane:INFO] - Time taken to add initial pools: 0.09682750701904297


In [25]:
def init_bot(mgr: Manager) -> CarbonBot:
    """
    Initializes the bot.

    Parameters
    ----------
    mgr : Manager
        The manager object.

    Returns
    -------
    CarbonBot
        The bot object.
    """
    mgr.cfg.logger.info("Initializing the bot...")
    bot = CarbonBot(ConfigObj=mgr.cfg)
    bot.db = db
    bot.db.mgr = mgr
    assert isinstance(
        bot.db, QueryInterface
    ), "QueryInterface not initialized correctly"
    return bot

In [26]:
bot = init_bot(mgr)

2023-07-09 17:27:40,554 [fastlane:INFO] - Initializing the bot...


In [27]:
# add data cleanup steps from main.py
bot.db.handle_token_key_cleanup()
bot.db.remove_unmapped_uniswap_v2_pools()
bot.db.remove_zero_liquidity_pools()
bot.db.remove_unsupported_exchanges()

2023-07-09 17:27:41,172 [fastlane:INFO] - Removed 0 unmapped uniswap_v2/sushi pools. 463 uniswap_v2/sushi pools remaining
2023-07-09 17:27:41,172 [fastlane:INFO] - Unmapped uniswap_v2/sushi pools:
2023-07-09 17:27:41,177 [fastlane:INFO] - uniswap_v3: 0
2023-07-09 17:27:41,178 [fastlane:INFO] - uniswap_v2: 0
2023-07-09 17:27:41,178 [fastlane:INFO] - sushiswap_v2: 0
2023-07-09 17:27:41,179 [fastlane:INFO] - uniswap_v3: 181
2023-07-09 17:27:41,180 [fastlane:INFO] - sushiswap_v2: 33
2023-07-09 17:27:41,181 [fastlane:INFO] - uniswap_v2: 0
2023-07-09 17:27:41,181 [fastlane:INFO] - bancor_v2: 0
2023-07-09 17:27:41,182 [fastlane:INFO] - bancor_v3: 34
2023-07-09 17:27:41,183 [fastlane:INFO] - carbon_v1: 215
2023-07-09 17:27:41,186 [fastlane:INFO] - uniswap_v3_zero_liquidity_pools: 0
2023-07-09 17:27:41,187 [fastlane:INFO] - sushiswap_v2_zero_liquidity_pools: 0
2023-07-09 17:27:41,188 [fastlane:INFO] - uniswap_v2_zero_liquidity_pools: 0
2023-07-09 17:27:41,189 [fastlane:INFO] - bancor_v2_zero_li

In [28]:
tokens = bot.db.get_tokens()

In [29]:
ADDRDEC = {t.key: (t.address, int(t.decimals)) for t in tokens if not math.isnan(t.decimals)}
# ADDRDEC = {t.key: (t.address, int(t.decimals)) for t in tokens}

In [30]:

print(len(ADDRDEC))

222


In [31]:
flashloan_tokens = bot.setup_flashloan_tokens(["BNT-FF1C"])
CCm = bot.setup_CCm(None)

In [32]:
pools = db.get_pool_data_with_tokens()

In [33]:
print(len(pools))

463


In [34]:
print(bot.db.mgr)

Manager(web3=<web3.main.Web3 object at 0x0000023282952BF0>, cfg=Config(network=_ConfigNetworkMainnet(), db=_ConfigDBPostgres(), logger=_ConfigLoggerDefault(), provider=_ConfigProviderAlchemy()), pool_data=[{'cid': '0x06b295766e941eb449be6a47d11466a50debbacc20638269523dac448fd210d4', 'last_updated': nan, 'last_updated_block': 0.0, 'descr': 'uniswap_v3 WETH-6Cc2/LHINU-038d 3000', 'pair_name': 'WETH-6Cc2/LHINU-038d', 'exchange_name': 'uniswap_v3', 'fee': 3000, 'fee_float': 0.003, 'address': '0xc5BBA4469eD5B55eE21228C9E7261816081C4Bfb', 'anchor': nan, 'tkn0_address': '0xC02aaA39b223FE8D0A0e5C4F27eAD9083C756Cc2', 'tkn1_address': '0xCeDefE438860D2789dA6419b3a19cEcE2A41038d', 'tkn0_key': 'WETH-6Cc2', 'tkn1_key': 'LHINU-038d', 'tkn0_decimals': 18.0, 'tkn1_decimals': 18.0, 'exchange_id': 4.0, 'tkn0_symbol': 'WETH', 'tkn1_symbol': 'LHINU', 'timestamp': nan, 'tkn0_balance': nan, 'tkn1_balance': nan, 'liquidity': nan, 'sqrt_price_q96': nan, 'tick': nan, 'tick_spacing': 60, 'exchange': 'uniswap_v3'

In [35]:
# single = bot.run_single_mode(flashloan_tokens, CCm, arb_mode, run_data_validator=True)

single = bot._run(flashloan_tokens=flashloan_tokens, CCm=CCm, arb_mode=arb_mode, data_validator=True, result="calc_trade_instr")


2023-07-09 17:27:42,200 [fastlane:WARNING] - base_exchange must be bancor_v3 for single_triangle_bancor3, setting it to bancor_v3
2023-07-09 17:27:42,201 [fastlane:INFO] - flashloan_tokens for arb_mode=single_triangle_bancor3 will be overwritten. 
c:\Users\Kveen\PycharmProjects\carbonbot\fastlane_bot\tools\optimizer.py:1310: RuntimeWarning: divide by zero encountered in scalar divide
  price = get(p, tokens_ix.get(tknb)) / get(p, tokens_ix.get(tknq))
c:\Users\Kveen\PycharmProjects\carbonbot\fastlane_bot\tools\optimizer.py:1310: RuntimeWarning: divide by zero encountered in scalar divide
  price = get(p, tokens_ix.get(tknb)) / get(p, tokens_ix.get(tknq))
c:\Users\Kveen\PycharmProjects\carbonbot\fastlane_bot\tools\optimizer.py:1310: RuntimeWarning: divide by zero encountered in scalar divide
  price = get(p, tokens_ix.get(tknb)) / get(p, tokens_ix.get(tknq))
c:\Users\Kveen\PycharmProjects\carbonbot\fastlane_bot\tools\optimizer.py:1157: RuntimeWarning: invalid value encountered in subtrac

pool_cid = 0xf369ec02502a48fe5b8f0af8a0e712e9b3db0119abd2cd1b6f592125de74aefa
current_pool = PoolAndTokens(ConfigObj=Config(network=_ConfigNetworkMainnet(), db=_ConfigDBPostgres(), logger=_ConfigLoggerDefault(), provider=_ConfigProviderAlchemy()), id=236, cid='0xf369ec02502a48fe5b8f0af8a0e712e9b3db0119abd2cd1b6f592125de74aefa', last_updated=nan, last_updated_block=17656137, descr='bancor_v3 BNT-FF1C/RPL-A51f 0.000', pair_name='BNT-FF1C/RPL-A51f', exchange_name='bancor_v3', fee='0.000', fee_float=0.0, tkn0_balance=135623681693338392099781, tkn1_balance=1440648360015295689515, z_0=0, y_0=0, A_0=0, B_0=0, z_1=0, y_1=0, A_1=0, B_1=0, sqrt_price_q96=nan, tick=nan, tick_spacing=0, liquidity=nan, address='0xC011a73ee8576Fb46F5E1c5751cA3B9Fe0af2a6F', anchor=nan, tkn0='BNT', tkn1='RPL', tkn0_address='0x1F573D6Fb3F13d689FF844B4cE37794d79a7FF1C', tkn0_decimals=18.0, tkn1_address='0xD33526068D116cE69F19A9ee46F0bd304F21A51f', tkn1_decimals=18.0, tkn0_key='BNT-FF1C', tkn1_key='RPL-A51f')
pool_info =

2023-07-09 17:27:43,564 [fastlane:INFO] - [bot.py validate] pool_cid: 0xf369ec02502a48fe5b8f0af8a0e712e9b3db0119abd2cd1b6f592125de74aefa
2023-07-09 17:27:43,565 [fastlane:INFO] - [bot.py validate] fetched_pool: bancor_v3
2023-07-09 17:27:43,566 [fastlane:INFO] - [bot.py validate] fetched_pool: {'cid': '0xf369ec02502a48fe5b8f0af8a0e712e9b3db0119abd2cd1b6f592125de74aefa', 'id': 236, 'address': '0xC011a73ee8576Fb46F5E1c5751cA3B9Fe0af2a6F', 'pair_name': 'BNT-FF1C/RPL-A51f', 'exchange_name': 'bancor_v3', 'tkn0_address': '0x1F573D6Fb3F13d689FF844B4cE37794d79a7FF1C', 'tkn1_address': '0xD33526068D116cE69F19A9ee46F0bd304F21A51f', 'tkn0_key': 'BNT-FF1C', 'tkn1_key': 'RPL-A51f', 'args': {'id': '0xf369ec02502a48fe5b8f0af8a0e712e9b3db0119abd2cd1b6f592125de74aefa'}, 'last_updated_block': 17656738, 'fee': '0.000', 'fee_float': 0.0, 'tkn0_balance': 135623681693338392099781, 'tkn1_balance': 1440648360015295689515}


pool_cid = 0x748ab2bef0d97e5a044268626e6c9c104bab818605d44f650fdeaa03a3c742d2
current_pool = PoolAndTokens(ConfigObj=Config(network=_ConfigNetworkMainnet(), db=_ConfigDBPostgres(), logger=_ConfigLoggerDefault(), provider=_ConfigProviderAlchemy()), id=223, cid='0x748ab2bef0d97e5a044268626e6c9c104bab818605d44f650fdeaa03a3c742d2', last_updated=nan, last_updated_block=17656137, descr='bancor_v3 BNT-FF1C/ETH-EEeE 0.000', pair_name='BNT-FF1C/ETH-EEeE', exchange_name='bancor_v3', fee='0.000', fee_float=0.0, tkn0_balance=16872052302846033751403692, tkn1_balance=3556518861765761923784, z_0=0, y_0=0, A_0=0, B_0=0, z_1=0, y_1=0, A_1=0, B_1=0, sqrt_price_q96=nan, tick=nan, tick_spacing=0, liquidity=nan, address='0x7Fc66500c84A76Ad7e9c93437bFc5Ac33E2DDaE9', anchor=nan, tkn0='BNT', tkn1='ETH', tkn0_address='0x1F573D6Fb3F13d689FF844B4cE37794d79a7FF1C', tkn0_decimals=18.0, tkn1_address='0xEeeeeEeeeEeEeeEeEeEeeEEEeeeeEeeeeeeeEEeE', tkn1_decimals=18.0, tkn0_key='BNT-FF1C', tkn1_key='ETH-EEeE')
pool_info

2023-07-09 17:27:44,050 [fastlane:INFO] - [bot.py validate] pool_cid: 0x748ab2bef0d97e5a044268626e6c9c104bab818605d44f650fdeaa03a3c742d2
2023-07-09 17:27:44,050 [fastlane:INFO] - [bot.py validate] fetched_pool: bancor_v3
2023-07-09 17:27:44,051 [fastlane:INFO] - [bot.py validate] fetched_pool: {'cid': '0x748ab2bef0d97e5a044268626e6c9c104bab818605d44f650fdeaa03a3c742d2', 'id': 223, 'address': '0x7Fc66500c84A76Ad7e9c93437bFc5Ac33E2DDaE9', 'pair_name': 'BNT-FF1C/ETH-EEeE', 'exchange_name': 'bancor_v3', 'tkn0_address': '0x1F573D6Fb3F13d689FF844B4cE37794d79a7FF1C', 'tkn1_address': '0xEeeeeEeeeEeEeeEeEeEeeEEEeeeeEeeeeeeeEEeE', 'tkn0_key': 'BNT-FF1C', 'tkn1_key': 'ETH-EEeE', 'args': {'id': '0x748ab2bef0d97e5a044268626e6c9c104bab818605d44f650fdeaa03a3c742d2'}, 'last_updated_block': 17656738, 'fee': '0.000', 'fee_float': 0.0, 'tkn0_balance': 16870346009234744317665943, 'tkn1_balance': 3556878861765761923784}


AssertionError: Current data for Constant Product pool 0x748ab2bef0d97e5a044268626e6c9c104bab818605d44f650fdeaa03a3c742d2 on bancor_v3, tkn0 balance 16872052302846033751403692 does not match actual balance: 16870346009234744317665943

In [ ]:
# bot.run(
#                 polling_interval=12,
#                 flashloan_tokens=["BNT"],
#                 mode="single",
#                 arb_mode="bancor_v3",
#                 run_data_validator=True
#             )